In [15]:
import folium
import requests
import osmnx as ox
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.colors as mcolors

from shapely.geometry import Point
from datetime import datetime, timezone
from math import radians, sin, cos, sqrt, atan2

In [9]:
class RouteFeatureExtractor:
    """
    Extracts OSM, weather and geometric features from a GPS route.
    Features are aggregated into fixed-length segments (~100 m).
    """
    
    def __init__(self, gps_route, weather_api_key=None):

        self.weather_api_key = weather_api_key

        self.df = pd.DataFrame(gps_route, columns=["lat", "lon"])
        self.df["Hour"] = datetime.now(timezone.utc).hour

        # Distancias
        self.df["Delta_d_raw"] = 0.0       # punto a punto [m]
        self.df["Trip_distance"] = 0.0     # acumulada [m]
        self.df["Delta_d"] = 0.0           # delta entre segmentos

        self.df["Hum"] = np.nan            # Humedad (%)
        self.df["Elevation"] = np.nan
        self.df["Slope"] = 0.0             # grados

        # Variables binarias de la ruta 
        self.df["primary"] = 0
        self.df["residential"] = 0
        self.df["secondary"] = 0
        self.df["crossing"] = 0
        self.df["tertiary"] = 0
        self.df["give_way"] = 0

    # Distancia entre dos coordenadas
    def _haversine_m(self, p1, p2):
        R = 6371000.0
        lat1, lon1 = radians(p1[0]), radians(p1[1])
        lat2, lon2 = radians(p2[0]), radians(p2[1])

        dlat = lat2 - lat1
        dlon = lon2 - lon1

        a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
        return 2 * R * atan2(sqrt(a), sqrt(1 - a))

    # Distancias entre puntos consecutivos
    def compute_distances(self):

        deltas = [0.0]

        for i in range(1, len(self.df)):
            p1 = self.df.loc[i - 1, ["lat", "lon"]].values
            p2 = self.df.loc[i, ["lat", "lon"]].values
            deltas.append(self._haversine_m(p1, p2))

        self.df["Delta_d_raw"] = deltas
        self.df["Trip_distance"] = np.cumsum(deltas)

    # Segmenntacion de la ruta en tramos de 100 metros
    def assign_segments(self, segment_length_m=100):

        segment_ids = []
        current_segment = 0
        acc_dist = 0.0

        for d in self.df["Delta_d_raw"]:
            if acc_dist >= segment_length_m:
                current_segment += 1
                acc_dist = 0.0

            segment_ids.append(current_segment)
            acc_dist += d

        self.df["segment_id"] = segment_ids

    # Diferencia de distancia entre segmentos
    def compute_delta_d_per_segment(self):

        seg_lengths = (
            self.df
            .groupby("segment_id")["Delta_d_raw"]
            .sum()
            .reset_index(name="segment_length")
        )

        seg_lengths["cum_dist"] = seg_lengths["segment_length"].cumsum()
        seg_lengths["Delta_d"] = seg_lengths["cum_dist"].diff()
        seg_lengths.loc[0, "Delta_d"] = 0.0

        delta_map = dict(
            zip(seg_lengths["segment_id"], seg_lengths["Delta_d"])
        )

        self.df["Delta_d"] = self.df["segment_id"].map(delta_map)

    # Obtención de datos meteorológicos (Hum %) desde World Weather Online
    def fetch_weather(self):

        if self.weather_api_key is None:
            return

        try:
            lat, lon = self.df.loc[0, ["lat", "lon"]]

            r = requests.get(
                "https://api.worldweatheronline.com/premium/v1/past-weather.ashx",
                params={
                    "key": self.weather_api_key,
                    "q": f"{lat},{lon}",
                    "format": "json",
                    "date": datetime.now(timezone.utc).strftime("%Y-%m-%d"),
                    "tp": 24,
                },
                timeout=10
            )
            r.raise_for_status()

            hum = float(r.json()["data"]["weather"][0]["hourly"][0]["humidity"])
            self.df["Hum"] = hum

        except Exception as e:
            print("Weather API error:", e)


    # Obtención de features de la ruta desde OSM
    def fetch_osm_features(self):

        try:
            center = (self.df["lat"].mean(), self.df["lon"].mean())

            G = ox.graph_from_point(center, dist=1500, network_type="drive")
            nodes, edges = ox.graph_to_gdfs(G)

            utm_crs = ox.projection.project_gdf(nodes).crs
            nodes_p = nodes.to_crs(utm_crs)
            edges_p = edges.to_crs(utm_crs)

            for i, row in self.df.iterrows():

                p = Point(row["lon"], row["lat"])
                p_proj = ox.projection.project_geometry(p, to_crs=utm_crs)[0]

                edge_idx = edges_p.distance(p_proj).idxmin()
                highway = edges.loc[edge_idx].get("highway", "")

                if isinstance(highway, list):
                    highway = highway[0]

                if highway == "primary":
                    self.df.loc[i, "primary"] = 1
                elif highway == "residential":
                    self.df.loc[i, "residential"] = 1
                elif highway == "secondary":
                    self.df.loc[i, "secondary"] = 1

                node_idx = nodes_p.distance(p_proj).idxmin()
                node_hw = nodes.loc[node_idx].get("highway", "")

                if node_hw == "crossing":
                    self.df.loc[i, "crossing"] = 1
                elif node_hw == "tertiary":
                    self.df.loc[i, "tertiary"] = 1
                elif node_hw == "give_way":
                    self.df.loc[i, "give_way"] = 1

        except Exception as e:
            print("OSM extraction error:", e)


    # Elevación por segmento
    # Se consulta la API para el primer y último punto de cada segmento
    def fetch_elevation_for_segments(self):

        self.df["Elevation_start"] = np.nan
        self.df["Elevation_end"] = np.nan

        for seg_id, group in self.df.groupby("segment_id"):

            if len(group) < 2:
                continue

            p0 = group.iloc[0]
            p1 = group.iloc[-1]

            loc = f"{p0.lat},{p0.lon}|{p1.lat},{p1.lon}"

            r = requests.get(
                "https://api.open-elevation.com/api/v1/lookup",
                params={"locations": loc},
                timeout=10
            )
            r.raise_for_status()
            res = r.json()["results"]
            self.df.loc[group.index[0], "Elevation_start"] = res[0]["elevation"]
            self.df.loc[group.index[-1], "Elevation_end"] = res[1]["elevation"]

    # Slope por segmento [°]
    # Se calcula entre el primer y último punto de cada segmento
    def compute_slope_per_segment(self):

        slope_map = {}

        for seg_id, group in self.df.groupby("segment_id"):

            if len(group) < 2:
                slope_map[seg_id] = 0.0
                continue

            z0 = group["Elevation_start"].iloc[0]
            z1 = group["Elevation_end"].iloc[-1]

            if np.isnan(z0) or np.isnan(z1):
                slope_map[seg_id] = 0.0
                continue

            d_seg = (
                group["Trip_distance"].iloc[-1]
                - group["Trip_distance"].iloc[0]
            )

            if d_seg <= 0:
                slope_map[seg_id] = 0.0
                continue

            slope_deg = np.degrees(np.arctan((z1 - z0) / d_seg))

            slope_map[seg_id] = np.clip(slope_deg, -15, 15)

        self.df["Slope"] = self.df["segment_id"].map(slope_map)

    # Construcción del dataframe
    def aggregate_segments(self):

        agg = {
            "Hour": "mean",
            "Trip_distance": "mean",
            "Delta_d": "mean",
            "Hum": "mean",
            "Slope": "mean",
            "primary": "max",
            "residential": "max",
            "secondary": "max",
            "crossing": "max",
            "tertiary": "max",
            "give_way": "max",
        }

        return (
            self.df
            .groupby("segment_id", as_index=False)
            .agg(agg)
        )

    # Ejecutar todo el pipeline
    def run_all(self):

        self.compute_distances()
        self.assign_segments()
        self.compute_delta_d_per_segment()

        self.fetch_weather()
        self.fetch_osm_features()

        self.fetch_elevation_for_segments()
        self.compute_slope_per_segment()

        return self.aggregate_segments()

## Validamos con viajes de Ann Arbor

In [10]:
df = pd.read_csv('ev_data_processed.csv', low_memory=False)
df.columns = [c.lower() for c in df.columns]

required_cols = {"vehid", "trip", "matched_latitude", "matched_longitude"}
if not required_cols.issubset(df.columns):
    raise ValueError(
        f"El dataset debe contener las columnas: {required_cols}"
    )

veh_ids = sorted(df["vehid"].unique())

print("\nVehId disponibles en el dataset:")
print([int(v) for v in veh_ids])

vehid_sel = int(input("\nIngrese el VehId que desea analizar: "))

if vehid_sel not in veh_ids:
    raise ValueError("El VehId seleccionado no existe en el dataset.")

trip_ids = sorted(df.loc[df["vehid"] == vehid_sel, "trip"].unique())

print(f"\nTrips disponibles para el VehId {vehid_sel}:")
print([int(t) for t in trip_ids])

trip_sel = int(input("\nIngrese el Trip que desea analizar: "))

if trip_sel not in trip_ids:
    raise ValueError("El Trip seleccionado no existe para el VehId indicado.")

df_trip = (
    df[(df["vehid"] == vehid_sel) & (df["trip"] == trip_sel)]
    .sort_index()
)

gps_route = list(
    zip(
        df_trip["latitude"].astype(float),
        df_trip["longitude"].astype(float)
    )
)

if len(gps_route) < 2:
    raise ValueError("La ruta seleccionada no contiene suficientes puntos GPS.")

print("\nRuta GPS extraída correctamente.")
print(f"Número total de puntos GPS: {len(gps_route)}")
print(
    f"Punto inicial: "
    f"({gps_route[0][0]:.6f}, {gps_route[0][1]:.6f})"
)
print(
    f"Punto final: "
    f"({gps_route[-1][0]:.6f}, {gps_route[-1][1]:.6f})"
)


VehId disponibles en el dataset:
[10, 455, 541]

Trips disponibles para el VehId 455:
[554, 565, 568, 575, 588, 596, 600, 601, 603, 616, 625, 627, 630, 632, 635, 636, 646, 658, 659, 668, 669, 674, 678, 690, 694, 702, 719, 728, 735, 736, 738, 739, 755, 757, 772, 775, 778, 780, 787, 792, 795, 799, 803, 808, 816, 825, 869, 876, 883, 887, 896, 900, 901, 912, 915, 916, 936, 937, 941, 956, 960, 970, 982, 983, 986, 989, 1001, 1006, 1009, 1026, 1034, 1035, 1049, 1064, 1067, 1070, 1073, 1075, 1076, 1083, 1100, 1108, 1110, 1111, 1113, 1117, 1139, 1143, 1149, 1154, 1160, 1168, 1175, 1179, 1184, 1197, 1198, 1204, 1212, 1221, 1222, 1243, 1245, 1261, 1262, 1263, 1292, 1304, 1306, 1310, 1320, 1323, 1338, 1339, 1340, 1360, 1363, 1373, 1380, 1383, 1384, 1402, 1405, 1406, 1409, 1410, 1413, 1418, 1421, 1424, 1427, 1429, 1435, 1453, 1457, 1461, 1469, 1474, 1492, 1493, 1496, 1509, 1510, 1511, 1516, 1520, 1522, 1528, 1531, 1532, 1533, 1553, 1561, 1562, 1567, 1573, 1575, 1582, 1586, 1589, 1591, 1593, 1594, 

In [11]:
extractor = RouteFeatureExtractor(gps_route, weather_api_key="67a922066b844919a0a191058252705")
df_segments = extractor.run_all()

In [12]:
df_segments.describe()

segment_id   Hour  Trip_distance     Delta_d    Hum       Slope  \
count    140.0000  140.0     140.000000  140.000000  140.0  140.000000   
mean      69.5000   19.0    8154.734847  115.450535   80.0    0.041175   
std       40.5586    0.0    4767.229212   18.067284    0.0    2.405922   
min        0.0000   19.0      34.688540    0.000000   80.0  -15.000000   
25%       34.7500   19.0    4126.687679  106.912269   80.0    0.000000   
50%       69.5000   19.0    8144.253615  114.532826   80.0    0.000000   
75%      104.2500   19.0   12193.914138  125.902006   80.0    1.019996   
max      139.0000   19.0   16266.529691  145.332146   80.0    8.315438   

          primary  residential   secondary  crossing  tertiary  give_way  
count  140.000000   140.000000  140.000000     140.0     140.0     140.0  
mean     0.085714     0.521429    0.335714       0.0       0.0       0.0  
std      0.280947     0.501334    0.473935       0.0       0.0       0.0  
min      0.000000     0.000000    0.000000       0.0       0.0       0.0  
25%      0.000000     0.000000    0.000000       0.0       0.0       0.0  
50%      0.000000     1.000000    0.000000       0.0       0.0       0.0  
75%      0.000000     1.000000    1.000000       0.0       0.0       0.0  
max      1.000000     1.000000    1.000000       0.0       0.0       0.0

In [13]:
df_segments.to_csv(f"veh{vehid_sel}_trip{trip_sel}_features.csv", index=False)

In [17]:
trip_df = df_trip[
    df_trip["matched_latitude"].notna() &
    df_trip["matched_longitude"].notna()
].copy().reset_index(drop=True)

if len(trip_df) < 2:
    raise ValueError("El viaje no tiene suficientes puntos GPS válidos.")

def haversine_m(lat1, lon1, lat2, lon2):
    R = 6371000.0
    lat1, lon1 = radians(lat1), radians(lon1)
    lat2, lon2 = radians(lat2), radians(lon2)

    dlat = lat2 - lat1
    dlon = lon2 - lon1

    a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
    return 2 * R * atan2(sqrt(a), sqrt(1 - a))


delta_d = [0.0]
for i in range(1, len(trip_df)):
    delta_d.append(
        haversine_m(
            trip_df.loc[i - 1, "matched_latitude"],
            trip_df.loc[i - 1, "matched_longitude"],
            trip_df.loc[i, "matched_latitude"],
            trip_df.loc[i, "matched_longitude"],
        )
    )

trip_df["delta_d"] = delta_d
trip_df["cum_distance_m"] = np.cumsum(delta_d)

segment_length = 100.0  # metros

segment_ids = []
current_segment = 0
accum = 0.0

for d in trip_df["delta_d"]:
    if accum >= segment_length:
        current_segment += 1
        accum = 0.0
    segment_ids.append(current_segment)
    accum += d

trip_df["segment_id"] = segment_ids

n_segments = trip_df["segment_id"].nunique()
print(f"Número de segmentos: {n_segments}")

center = (
    trip_df["matched_latitude"].mean(),
    trip_df["matched_longitude"].mean()
)

m = folium.Map(location=center, zoom_start=13, tiles="OpenStreetMap")

cmap = plt.colormaps["tab20"]

for seg_id, group in trip_df.groupby("segment_id"):

    coords_seg = list(
        zip(group["matched_latitude"], group["matched_longitude"])
    )

    if len(coords_seg) < 2:
        continue

    color = mcolors.to_hex(cmap(seg_id % cmap.N))

    folium.PolyLine(
        coords_seg,
        color=color,
        weight=6,
        opacity=0.9,
        tooltip=f"Segmento {seg_id}"
    ).add_to(m)

threshold_m = 300

for i, row in trip_df.iterrows():

    is_jump = row["delta_d"] > threshold_m

    folium.CircleMarker(
        location=(row["matched_latitude"], row["matched_longitude"]),
        radius=6 if is_jump else 4,
        color="red" if is_jump else "black",
        fill=True,
        fill_opacity=0.8,
        tooltip=(
            f"Idx: {i}<br>"
            f"Segmento: {row['segment_id']}<br>"
            f"Δdist: {row['delta_d']:.1f} m<br>"
            f"Dist acum: {row['cum_distance_m']:.1f} m"
        )
    ).add_to(m)

folium.Marker(
    (trip_df.loc[0, "matched_latitude"], trip_df.loc[0, "matched_longitude"]),
    icon=folium.Icon(color="green", icon="play"),
    tooltip="Inicio"
).add_to(m)

folium.Marker(
    (trip_df.loc[len(trip_df)-1, "matched_latitude"],
     trip_df.loc[len(trip_df)-1, "matched_longitude"]),
    icon=folium.Icon(color="red", icon="stop"),
    tooltip="Fin"
).add_to(m)

m

Número de segmentos: 138
